## F1 ROUGE score on QnA Dataset with the Base model

In [ ]:
pip -q install accelerate bitsandbytes


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 270.9/270.9 kB 830.1 kB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 105.0/105.0 MB 5.8 MB/s eta 0:00:00


In [ ]:
from transformers import AutoTokenizer, AutoModelForCausalLM
import torch
import json

In [ ]:
print(torch.__version__)
print(torch.cuda.is_available())


2.1.0+cu121
True


In [ ]:
from huggingface_hub import notebook_login
notebook_login()

In [ ]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'
print(f"Using device: {device}")


# Function to calculate F1 score
def calculate_f1_score(predicted_answer, ground_truth_answer):
    predicted_tokens = set(predicted_answer.split())
    ground_truth_tokens = set(ground_truth_answer.split())
    common_tokens = predicted_tokens.intersection(ground_truth_tokens)
    if len(predicted_tokens) == 0 or len(ground_truth_tokens) == 0:
        return 0
    precision = len(common_tokens) / len(predicted_tokens)
    recall = len(common_tokens) / len(ground_truth_tokens)
    if precision + recall == 0:
        return 0
    return 2 * (precision * recall) / (precision + recall)


# Load the LLaMA 2 model and tokenizer
model_name = "meta-llama/Llama-2-7b-chat-hf"
model = AutoModelForCausalLM.from_pretrained(model_name, load_in_8bit=True, device_map='cuda:0', use_cache=False)
tokenizer = AutoTokenizer.from_pretrained(model_name)


# Function to predict answers using the model, modified to use GPU if available
def predict_answer(input_text):
    inputs = tokenizer.encode(input_text, return_tensors="pt").to(device)
    outputs = model.generate(inputs, max_length=192, num_return_sequences=1)
    answer = tokenizer.decode(outputs[0], skip_special_tokens=True)
    return answer


# Function to load data and prepare it
def load_and_prepare_data(file_path):
    with open(file_path, 'r', encoding='utf-8') as file:
        data = json.load(file)
    prepared_data = []
    for item in data:
        input_text = item['instruction'] + " " + item['input_content'] if item['input_content'] else item['instruction']
        prepared_data.append((input_text, item['expected_output']))
    return prepared_data


# Load and prepare your dataset
file_path = 'my_data_QnA.json'
test_dataset = load_and_prepare_data(file_path)


# Evaluate the model
total_f1_score = 0
for input_text, correct_output in test_dataset:
    predicted_output = predict_answer(input_text)
    f1_score = calculate_f1_score(predicted_output, correct_output)
    total_f1_score += f1_score
    print(f"Input: {input_text}\nPredicted Output: {predicted_output}\nCorrect Output: {correct_output}\nF1 Score: {f1_score}\n")


average_f1_score = total_f1_score / len(test_dataset)
print(f"Average F1 Score: {average_f1_score}")

Using device: cuda


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/614 [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/26.8k [00:00<?, ?B/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/9.98G [00:00<?, ?B/s]

...

/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1281: UserWarning: Input length of input_ids is 195, but `max_length` is set to 192. This can lead to unexpected behavior. You should consider increasing `max_new_tokens`.
  warnings.warn(


Input: Highlight the differences between Artificial Neural Network (ANN) and Biological Neural Network (BNN) Artificial Neural Networks (ANNs) and Biological Neural Networks (BNNs) share basic components but have significant differences. In terms of neurons, BNN neurons are more complex and diverse than ANNs. BNNs have multiple dendrites and axons, while ANNs typically have a single output. Synapses in ANNs have fixed connections with connection strength determined by weights, while BNN synapses have flexible connections that can be modified by learning and experience. Neural pathways in BNNs are highly complex and modifiable, while ANNs have simpler predetermined pathways. Overall, BNNs are more complex, adaptable, and capable of parallel processing, while ANNs are simpler and designed for specific tasks.
Predicted Output: Highlight the differences between Artificial Neural Network (ANN) and Biological Neural Network (BNN) Artificial Neural Networks (ANNs) and Biological Neural Networ

/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1281: UserWarning: Input length of input_ids is 238, but `max_length` is set to 192. This can lead to unexpected behavior. You should consider increasing `max_new_tokens`.
  warnings.warn(


Input: Provide a summary of the differences in parameters, computing, reliability, expertise, and operating environment between ANN and BNN ANN and BNN differ in various parameters, computing, reliability, expertise, and operating environment. In terms of structure, ANN consists of input, hidden layers, and output, while BNN has dendrites, synapses, axons, and cell bodies. ANN is suitable for very precise structures and formatted data, while BNN can tolerate ambiguity. ANN processors are complex and high-speed, while BNN processors are simple, low-speed, and parallel. ANN has separate memory from the processor, while BNN has integrated memory. ANN computing is centralized and sequential, while BNN is distributed, parallel, and self-learning. ANN is vulnerable to faults, while BNN is robust. ANN expertise lies in numerical and symbolic manipulations, while BNN expertise is in perceptual problems. ANN operates in well-defined environments, while BNN operates in poorly defined and unconst

KeyboardInterrupt: 

* We need to fine-tune the Base model with our custom dataset due to the poor F1 score we can see from above.